In [4]:
import os

In [5]:
path = r'D:\Projects\PIB Chatbot\Project_P\ScraperFiles\newFiles'

In [14]:
count = 0

In [15]:
for i in os.listdir(path):
    for j in os.listdir(os.path.join(path, i)):
        for k in os.listdir(os.path.join(path, i , j)):
            try:
                with open(os.path.join(path, i , j, k), 'r', encoding='utf-8') as f:
                    f.read()
                    f.close()
                    count+=1
            except Exception as e:
                print(k, 'Error' , e)
            

In [16]:
count

8008

In [8]:
from langchain.document_loaders import TextLoader
from langchain.schema import Document

directory = r"D:\Projects\PIB Chatbot\Project_P\ScraperFiles\newFiles"
documents = []

loaded = 0
unloaded = 0
for i in os.listdir(directory):
    for j in os.listdir(os.path.join(path, i)):
        for k in os.listdir(os.path.join(path, i , j)):
            try:
                if k.endswith(".txt"):
                    file_path = os.path.join(directory, i , j, k)
                    
                    # Create loader and load the document
                    loader = TextLoader(file_path, encoding='utf-8')
                    doc = loader.load()[0]
                    
                    # Add metadata (e.g., filename or custom data)
                    doc.metadata = {"source": k, "Ministry": j, "Month":i}
                    
                    documents.append(doc)
                    loaded+=1
            except Exception as e:
                print(k, 'Error' , e)
                unloaded+=1
print(loaded, " ", unloaded)                

1977   0


In [18]:
from langchain_text_splitters import RecursiveCharacterTextSplitter

text_splitter = RecursiveCharacterTextSplitter(
    chunk_size = 1000,
    chunk_overlap = 200,
    separators=[
        "\n\n",
        "\n"
    ]
)

In [19]:
chunks = text_splitter.split_documents(documents)

In [21]:
len(chunks)

59005

In [9]:
from langchain_huggingface import HuggingFaceEmbeddings

embeddings = HuggingFaceEmbeddings(model_name="sentence-transformers/paraphrase-MiniLM-L6-v2")

d:\Projects\PIB Chatbot\Project_P\.venv\lib\site-packages\transformers\tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [4]:
from langchain_pinecone import PineconeVectorStore
from pinecone import Pinecone, ServerlessSpec # Import Pinecone and ServerlessSpec
from dotenv import load_dotenv
import os

load_dotenv()

pinecone_api_key = os.getenv("PINECONE_API_KEY")  # Add your Pinecone API key 
gemini_api_key = os.getenv("GOOGLE_API_KEY")  # Add your Google Generative AI key

pinecone_api_key = pinecone_api_key # Use your API key
pc = Pinecone(api_key=pinecone_api_key)


In [22]:
load_dotenv()

True

In [23]:
gemini_api_key = os.getenv("GOOGLE_API_KEY") 

In [7]:
index_name = "pib"
existing_indexes = [index_info["name"] for index_info in pc.list_indexes()]

if index_name not in existing_indexes:
    pc.create_index(
        name=index_name,
        dimension=384,
        metric="cosine",
        spec=ServerlessSpec(cloud="aws", region="us-east-1")
    )

index = pc.Index(index_name)

In [10]:
vector_store = PineconeVectorStore(index=index, embedding=embeddings)

In [31]:
vector_store.add_documents(chunks)

['933e13f0-bea7-46fc-b369-e3afd58ef02f',
 '76a4fc23-28aa-4db3-9c06-431a9898fe63',
 '6bd679f1-43f1-444a-ba80-8208a35f5118',
 'bc1c3351-5245-4f37-92c2-673fa7a93bf6',
 'fd9a23a8-8153-4ec1-817e-f0a5ec1472e7',
 '0e84ce6d-7d6f-406d-8c43-94518b3e9dd4',
 '65d54383-cc4d-4170-aa22-a2365d8d82d3',
 '2408bb41-9e99-498a-8452-8bc20b91ef00',
 '30eede1f-346c-44ad-9d30-876216cb84ca',
 '26004bc3-8e55-4263-94a4-fd04c8ae42df',
 '079f358c-61c9-43ab-83e8-5aa152480e23',
 'dbb5796b-094e-4617-a114-4024bb7823fe',
 'ba1ca13b-5f9e-4ba5-a81c-634f73bb5d31',
 'd85d3199-3b49-4d6b-9e47-96b94107b2c4',
 'cc3087ca-0d1c-40e0-b87e-3ff8cad4c495',
 'cea78fd5-9115-4943-b7d8-f590517a26ed',
 '5f27af15-faff-4dad-a276-fb8d104eefe5',
 '7ccf599f-c1e3-4c01-abdb-fcb1d9d7a6dd',
 '668a43ea-b7fd-4f43-91b9-a01465259d6c',
 '31f4f256-733c-4ed7-af46-b3ba87935434',
 'a96fa141-0383-4dfa-aad4-fb2c31a93089',
 'c338593e-eb7f-4365-8ec4-11624e55b6db',
 '068c4b7e-02d4-4c79-8f3a-8efdb010f9de',
 '15228002-b7ec-401b-af27-1f8d379294dc',
 '7bd65120-6bcc-

In [19]:
retriever = vector_store.as_retriever(
    search_type="similarity_score_threshold",
    search_kwargs={"k": 4, "score_threshold": 0.7},
)

In [35]:
retriever.invoke('Tell me about Vice Admiral Atul Anand?')

[Document(id='bb92199b-8683-4c11-a527-83d63a10fd16', metadata={'Ministry': 'Ministry_of_Defence', 'Month': 'Jul23html', 'source': 'Vice_Admiral_Atul_Anand_takes_over_as_Ad.txt'}, page_content='Vice Admiral Atul Anand took over as Additional Secretary, Department of Military Affairs on July 03, 2023. The post was previously held by Lt Gen Anil Puri, who superannuated on February 28, 2023.\nVice Admiral Atul Anand was commissioned into the executive branch of the Indian Navy on January 01, 1988. He is an alumnus of National Defence Academy (71st Course, Delta Squadron); Defence Services Command and Staff College, Mirpur (Bangladesh) and National Defence College, New Delhi. He has also attended the Advanced Security Cooperation course at Asia Pacific Centre of Security Studies, Hawaii, USA.'),
 Document(id='37993645-4733-4e97-b074-ca0a2e4f4592', metadata={'Ministry': 'Ministry_of_Defence', 'Month': 'Apr23html', 'source': 'VICE_ADM_ATUL_ANAND_TAKES_OVER_AS_DIRECT.txt'}, page_content='Vice 

In [27]:
from langchain_google_genai import GoogleGenerativeAI

llm = GoogleGenerativeAI(
    model="gemini-1.5-flash",
    google_api_key=gemini_api_key,
    temperature=0.01, # HIGHER THE TEMP. LESSER THE ACCURACY OF THE MODEL
)

In [25]:
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough
from langchain_core.prompts import PromptTemplate

template = """Use the following pieces of context to answer the question at the end.
If you don't know the answer, just say that you don't know, don't try to make up an answer.
Use three sentences maximum and keep the answer as concise as possible.
Always say "thanks for asking!" at the end of the answer.

{context}

Question: {question}

Helpful Answer:"""


def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)


custom_rag_prompt = PromptTemplate.from_template(template)

rag_chain = (
    {"context": retriever | format_docs, "question": RunnablePassthrough()}
    | custom_rag_prompt
    | llm
    | StrOutputParser()
)



In [36]:
ans = rag_chain.invoke("Tell me in detail about Vice Admiral Atul Anand?")

In [37]:
print(ans)

Vice Admiral Atul Anand is a highly decorated officer in the Indian Navy, having received both the Ati Vishisht Seva Medal and the Vishisht Seva Medal. He assumed the role of Director General Naval Operations on April 1st, 2023, and has held several key appointments, including command of multiple ships and important staff positions. He is an alumnus of the National Defence Academy and has a strong educational background, including a Master's in Defence Studies and an MPhil in Defence and Strategic Studies. Thanks for asking! 



In [10]:
from langchain_experimental.text_splitter import SemanticChunker
import os


In [17]:
from langchain.document_loaders import TextLoader


directory = r"D:\Projects\PIB Chatbot\Project_P\ScraperFiles\newFiles"
documents = []

loaded = 0
unloaded = 0
for i in os.listdir(directory):
    for j in os.listdir(os.path.join(directory, i)):
        for k in os.listdir(os.path.join(directory, i , j)):
            try:
                if k.endswith(".txt"):
                    file_path = os.path.join(directory, i , j, k)
                    
                    # Create loader and load the document
                    loader = TextLoader(file_path, encoding='utf-8')
                    doc = loader.load()[0]
                    
                    # Add metadata (e.g., filename or custom data)
                    doc.metadata = {"source": k, "Ministry": j, "Month":i}
                    
                    documents.append(doc)
                    loaded+=1
            except Exception as e:
                print(k, 'Error' , e)
                unloaded+=1
print(loaded, " ", unloaded)                

8008   0


In [19]:
from langchain_huggingface import HuggingFaceEmbeddings

embeddings = HuggingFaceEmbeddings(model_name="sentence-transformers/paraphrase-MiniLM-L6-v2")

d:\Projects\PIB Chatbot\Project_P\.venv\lib\site-packages\sentence_transformers\cross_encoder\CrossEncoder.py:13: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm, trange
d:\Projects\PIB Chatbot\Project_P\.venv\lib\site-packages\transformers\tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [20]:
text_splitter = SemanticChunker(embeddings, breakpoint_threshold_type='standard_deviation')

In [21]:
semanticChunks = text_splitter.split_documents(documents)

In [23]:
semanticChunks

[Document(metadata={'source': '5000_plus_Yoga_Enthusiasts_to_participat.txt', 'Ministry': 'AYUSH', 'Month': 'April24html'}, page_content="5000 plus Yoga Enthusiasts to participate in 75 days countdown to IDY- 2024\n\nThe Mahotsav will also witness active participation of Gram Pradhans, Anganwadi Workers & Asha Workers/Self Help Groups, Ayush Health & Wellness Centres, Resident Welfare Associations (RWAs), Women Welfare Organisations, School Children, and moreThe event will highlight the holistic health and wellness approach taking note of the Power of Yoga\nIn the ongoing journey of 100 days countdown of IDY 2024, more than 5000 Yoga Enthusiasts will be participating at 75th day countdown which is being held at Wadia College Sports Ground, Pune (Maharashtra) on 7th April, 2024. Focusing on holistic health and wellness approach and taking note of the power of Yoga, the Mahotsav will witness active participation of Gram Pradhans, Anganwadi Workers & Asha Workers/Self Help Groups, Ayush H

In [28]:
from dotenv import load_dotenv
from pinecone import Pinecone, ServerlessSpec
from langchain_pinecone import PineconeVectorStore

In [29]:
load_dotenv()
pinecone_api_key = os.getenv('PINECONE_API_KEY') # Use your API key
pc = Pinecone(api_key=pinecone_api_key)

In [30]:
index_name = "semanticpib"
existing_indexes = [index_info["name"] for index_info in pc.list_indexes()]

if index_name not in existing_indexes:
    pc.create_index(
        name=index_name,
        dimension=384,
        metric="cosine",
        spec=ServerlessSpec(cloud="aws", region="us-east-1")
    )
index = pc.Index(index_name)
vector_store = PineconeVectorStore(index=index, embedding=embeddings)
vector_store.add_documents(semanticChunks)

PineconeApiException: (400)
Reason: Bad Request
HTTP response headers: HTTPHeaderDict({'Date': 'Sat, 28 Sep 2024 20:01:53 GMT', 'Content-Type': 'application/json', 'Content-Length': '115', 'Connection': 'keep-alive', 'x-pinecone-request-latency-ms': '23', 'x-pinecone-request-id': '5010160277685443563', 'x-envoy-upstream-service-time': '1', 'server': 'envoy'})
HTTP response body: {"code":3,"message":"Metadata size is 51175 bytes, which exceeds the limit of 40960 bytes per vector","details":[]}


In [32]:
for i in documents:
    print(len(i.metadata['ministry']))

KeyError: 'ministry'

In [11]:
from langchain_community.vectorstores import Chroma
semantic_chunk_vectorstore = Chroma.from_documents(semanticChunks, embedding=embeddings)

: 

In [1]:
semantic_chunk_vectorstore

NameError: name 'semantic_chunk_vectorstore' is not defined

In [2]:
import requests
from bs4 import BeautifulSoup

# Define the URL
url = "https://pib.gov.in/allRel.aspx?reg=3&lang=1"

# Define headers
headers = {
    "accept": "text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.7",
    "accept-encoding": "gzip, deflate, br, zstd",
    "accept-language": "en-US,en;q=0.9,en-IN;q=0.8",
    "cache-control": "max-age=0",
    "connection": "keep-alive",
    "referer": "https://pib.gov.in/allRel.aspx?reg=3&lang=1",
    "sec-ch-ua": '"Microsoft Edge";v="131", "Chromium";v="131", "Not_A Brand";v="24"',
    "sec-ch-ua-mobile": "?0",
    "sec-ch-ua-platform": '"Windows"',
    "sec-fetch-dest": "document",
    "sec-fetch-mode": "navigate",
    "sec-fetch-site": "same-origin",
    "sec-fetch-user": "?1",
    "upgrade-insecure-requests": "1",
    "user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/131.0.0.0 Safari/537.36 Edg/131.0.0.0",
}

# Define cookies
cookies = {
    "ASP.NET_SessionId": "zpfhbfzvonufs302mjic5bre",
    "PIB_Accessibility": "Lang=1&Region=3",
    "_ga": "GA1.1.409721045.1733232314",
    "_ga_Q414Y0X6EE": "GS1.1.1733232314.1.1.1733232363.11.0.0",
    "_ga_QJJ6LZ8LHV": "GS1.1.1733232314.1.1.1733232363.0.0.0",
    "style": "null",
}

# Define payload
payload = {
    "reg": 3,
    "lang": 1,
}

# Make the GET request
response = requests.get(url, headers=headers, cookies=cookies, params=payload)

# Check if the request was successful
if response.status_code == 200:
    print("Request successful!")
    
    # Parse the HTML content
    soup = BeautifulSoup(response.content, "html.parser")
    
    # Extract desired information (Example: All links and titles)
    for link in soup.find_all("a"):
        href = link.get("href")
        text = link.get_text(strip=True)
        if href:
            print(f"Link: {href}, Text: {text}")
else:
    print(f"Failed to fetch the page. Status code: {response.status_code}")


Request successful!
Link: /index.aspx, Text: 
Link: /SubscribeRelease/SubscribeReleaseForm.aspx, Text: 
Link: /ViewRss.aspx, Text: 
Link: /screenReaderAcces.aspx, Text: Screen Reader Access
Link: /index.aspx, Text: 
Link: /SubscribeRelease/SubscribeReleaseForm.aspx, Text: 
Link: /ViewRss.aspx, Text: 
Link: #main-nav, Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: /SiteMap.aspx, Text: 
Link: /AdvanceSearch.aspx, Text: 
Link: /index.aspx, Text: 
Link: /index.aspx, Text: Press Information Bureau
Link: https://pib.gov.in/, Text: 
Link: /index.aspx, Text: 
Link: #, Text: About Us
Link: aboutpibn.aspx, Text: About PIB
Link: mainfunctions.aspx, Text: Main Functions
Link: organisationalsetup.aspx, Text: Organizational Setup
Link: heads

In [1]:
import requests
from bs4 import BeautifulSoup

# URL of the target page
url = "https://pib.gov.in/allRel.aspx?reg=3&lang=1"

# Headers
headers = {
    "accept": "text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.7",
    "accept-encoding": "gzip, deflate, br",
    "accept-language": "en-US,en;q=0.9,en-IN;q=0.8",
    "cache-control": "max-age=0",
    "connection": "keep-alive",
    "referer": "https://pib.gov.in/allRel.aspx?reg=3&lang=1",
    "sec-fetch-dest": "document",
    "sec-fetch-mode": "navigate",
    "sec-fetch-site": "same-origin",
    "sec-fetch-user": "?1",
    "upgrade-insecure-requests": "1",
    "user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/131.0.0.0 Safari/537.36 Edg/131.0.0.0"
}

# Start a session
session = requests.Session()

# Step 1: Initial GET request to fetch the hidden fields
response = session.get(url, headers=headers)
if response.status_code != 200:
    print("Failed to fetch the page.")
    exit()

# Parse the page content
soup = BeautifulSoup(response.content, "html.parser")

# Extract hidden fields
viewstate = soup.find("input", {"name": "__VIEWSTATE"})["value"]
eventvalidation = soup.find("input", {"name": "__EVENTVALIDATION"})["value"]
viewstategenerator = soup.find("input", {"name": "__VIEWSTATEGENERATOR"})["value"]

# Step 2: Define the POST payload
payload = {
    "script_HiddenField": "",
    "__EVENTTARGET": "ctl00$ContentPlaceHolder1$ddlMonth",
    "__EVENTARGUMENT": "",
    "__LASTFOCUS": "",
    "__VIEWSTATE": viewstate,
    "__VIEWSTATEGENERATOR": viewstategenerator,
    "__VIEWSTATEENCRYPTED": "",
    "__EVENTVALIDATION": eventvalidation,
    "ctl00$Bar1$ddlregion": "3",
    "ctl00$Bar1$ddlLang": "1",
    "ctl00$ContentPlaceHolder1$hydregionid": "3",
    "ctl00$ContentPlaceHolder1$hydLangid": "1",
    "ctl00$ContentPlaceHolder1$ddlMinistry": "0",
    "ctl00$ContentPlaceHolder1$ddlday": "0",  # Date set to 'All'
    "ctl00$ContentPlaceHolder1$ddlMonth": "11",
    "ctl00$ContentPlaceHolder1$ddlYear": "2024"
}

# Step 3: Submit the POST request
post_response = session.post(url, headers=headers, data=payload)
if post_response.status_code == 200:
    print("POST request successful!")
    
    # Parse the response content
    post_soup = BeautifulSoup(post_response.content, "html.parser")
    l = [loc.text.strip() for loc in soup.find_all('h3', class_ = 'font104')]
    allData = {}
    data = {}
    print(post_soup)

    # for i,j in zip(range(len(l)), l):
    #     names = []
    #     links = []
    #     for k in (soup.find_all('ul', class_ = 'leftul')[i].find_all('li')):
    #         names.append(k.text.strip())
    #         # print(names)

    #     for k in soup.find_all('ul', class_ = 'leftul')[i].find_all('li'):
    #         links.append('https://pib.gov.in/' + k.find('a').attrs['href'])
    #         # print(links)    
    #     data[j] = (names, links)
    # allData[nam] = data

# print(data)  
    # Example: Extract data from the response
    articles = post_soup.find_all("a")
    for article in articles:
        print(article.get("href"))
else:
    print(f"Failed to submit the form. Status code: {post_response.status_code}")


POST request successful!

<!DOCTYPE HTML>

<html lang="en">
<meta charset="utf-8"/>
<meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<meta content="public" http-equiv="Cache-control"/>
<meta content="Press Information Bureau (PIB) is the nodal agency of the Government of India to disseminate information to the print and electronic media on government policies, programmes, initiatives and achievements." name="description">
<meta content="Press Information Bureau, PIB, Government of India, Indian Government news, press releases, government updates, official news, India policies, national events, government schemes, Indian news portal" name="keywords"/>
<head id="Head1"><title>
	All Press Release: Press Information Bureau
</title><meta content="930300783691811" property="fb:app_id"/><link href="https://static.pib.gov.in/WriteReadData/specificdocs/photo/2022/apr/ph20224636301.jpg" rel="icon" type="image/jpg"/><link href="https://static.pib.gov.in/writereaddata/css/st

In [1]:
import requests
from bs4 import BeautifulSoup

# Define the URL
url = "https://pib.gov.in/allRel.aspx?reg=3&lang=1"

# Define headers
headers = {
    "accept": "text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.7",
    "accept-encoding": "gzip, deflate, br, zstd",
    "accept-language": "en-US,en;q=0.9,en-IN;q=0.8",
    "cache-control": "max-age=0",
    "connection": "keep-alive",
    "content-type": "application/x-www-form-urlencoded",
    "cookie": "PIB_Accessibility=Lang=1&Region=3; _ga=GA1.1.409721045.1733232314; _ga=GA1.1.409721045.1733232314; ASP.NET_SessionId=ndczp3xq4k0kipsjphyx4acq; Product=zdzyxwn1ka2vmaegxy5rpu5o; style=null; _ga_Q414Y0X6EE=GS1.1.1734534074.5.1.1734534325.59.0.0; _ga_QJJ6LZ8LHV=GS1.1.1734534075.5.1.1734534325.0.0.0",
    "host": "pib.gov.in",
    "origin": "https://pib.gov.in",
    "referer": "https://pib.gov.in/allRel.aspx?reg=3&lang=1",
    "sec-ch-ua": '"Microsoft Edge";v="131", "Chromium";v="131", "Not_A Brand";v="24"',
    "sec-ch-ua-mobile": "?0",
    "sec-ch-ua-platform": '"Windows"',
    "sec-fetch-dest": "document",
    "sec-fetch-mode": "navigate",
    "sec-fetch-site": "same-origin",
    "sec-fetch-user": "?1",
    "upgrade-insecure-requests": "1",
    "user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/131.0.0.0 Safari/537.36 Edg/131.0.0.0"
}

# Define payload
payload = {
    "ctl00$Bar1$ddlregion": 3,
    "ctl00$Bar1$ddlLang": 1,
    "ctl00$ContentPlaceHolder1$hydregionid": 3,
    "ctl00$ContentPlaceHolder1$hydLangid": 1,
    "ctl00$ContentPlaceHolder1$ddlMinistry": 0,
    "ctl00$ContentPlaceHolder1$ddlday": 0,
    "ctl00$ContentPlaceHolder1$ddlMonth": 12, 
    "ctl00$ContentPlaceHolder1$ddlYear": 2024
}

# Make the POST request
response = requests.post(url, headers=headers, data=payload)

# Check if the request was successful
if response.status_code == 200:
    print("Request successful!")
    
    # Parse the HTML content
    soup = BeautifulSoup(response.content, "html.parser")
    
    # Extract desired information (Example: All links and titles)
    for link in soup.find_all("a"):
        href = link.get("href")
        text = link.get_text(strip=True)
        if href:
            print(f"Link: {href}, Text: {text}")
else:
    print(f"Failed to fetch the page. Status code: {response.status_code}")

Request successful!
Link: /index.aspx, Text: 
Link: /SubscribeRelease/SubscribeReleaseForm.aspx, Text: 
Link: /ViewRss.aspx, Text: 
Link: /screenReaderAcces.aspx, Text: Screen Reader Access
Link: /index.aspx, Text: 
Link: /SubscribeRelease/SubscribeReleaseForm.aspx, Text: 
Link: /ViewRss.aspx, Text: 
Link: #main-nav, Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: javascript:void(0), Text: 
Link: /SiteMap.aspx, Text: 
Link: /AdvanceSearch.aspx, Text: 
Link: /index.aspx, Text: 
Link: /index.aspx, Text: Press Information Bureau
Link: https://pib.gov.in/, Text: 
Link: /index.aspx, Text: 
Link: #, Text: About Us
Link: aboutpibn.aspx, Text: About PIB
Link: mainfunctions.aspx, Text: Main Functions
Link: organisationalsetup.aspx, Text: Organizational Setup
Link: heads

In [4]:
import requests
from bs4 import BeautifulSoup

# Set up session and headers
session = requests.Session()
headers = {
    "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/132.0.0.0 Safari/537.36 Edg/132.0.0.0",
    "Origin": "https://pib.gov.in",
    "Referer": "https://pib.gov.in/allRel.aspx?reg=3&lang=1",
    "Sec-Fetch-Dest": "document",
    "Sec-Fetch-Mode": "navigate",
    "Sec-Fetch-Site": "same-origin",
}

# Initial GET request to get ViewState and validation fields
url = "https://pib.gov.in/allRel.aspx"
response = session.get(url, headers=headers)
soup = BeautifulSoup(response.text, 'html.parser')


In [5]:
soup


<!DOCTYPE HTML>

<html lang="en">
<meta charset="utf-8"/>
<meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<meta content="public" http-equiv="Cache-control"/>
<meta content="Press Information Bureau (PIB) is the nodal agency of the Government of India to disseminate information to the print and electronic media on government policies, programmes, initiatives and achievements." name="description">
<meta content="Press Information Bureau, PIB, Government of India, Indian Government news, press releases, government updates, official news, India policies, national events, government schemes, Indian news portal" name="keywords"/>
<head id="Head1"><title>
	All Press Release: Press Information Bureau
</title><meta content="930300783691811" property="fb:app_id"/><link href="https://static.pib.gov.in/WriteReadData/specificdocs/photo/2022/apr/ph20224636301.jpg" rel="icon" type="image/jpg"/><link href="https://static.pib.gov.in/writereaddata/css/style3.1.css" rel="styleshe

In [6]:
viewstate = soup.find('input', {'id': '__VIEWSTATE'})['value']
event_validation = soup.find('input', {'id': '__EVENTVALIDATION'})['value']
viewstate_generator = soup.find('input', {'id': '__VIEWSTATEGENERATOR'})['value']

In [9]:
viewstate_generator

'CBED066B'

In [10]:
payload = {
    "__EVENTTARGET": "ctl00$ContentPlaceHolder1$ddlday",
    "__EVENTARGUMENT": "",
    "__LASTFOCUS": "",
    "__VIEWSTATE": viewstate,
    "__VIEWSTATEGENERATOR": viewstate_generator,
    "__VIEWSTATEENCRYPTED": "",
    "__EVENTVALIDATION": event_validation,
    "ctl00$Bar1$ddlregion": "3",  # Region code
    "ctl00$Bar1$ddlLang": "1",    # Language code
    "ctl00$ContentPlaceHolder1$hydregionid": "3",
    "ctl00$ContentPlaceHolder1$hydLangid": "1",
    "ctl00$ContentPlaceHolder1$ddlMinistry": "0",  # 0 = All Ministry
    "ctl00$ContentPlaceHolder1$ddlday": "0",       # 0 = All Days
    "ctl00$ContentPlaceHolder1$ddlMonth": "1",     # 1 = January
    "ctl00$ContentPlaceHolder1$ddlYear": "2025",   # Selected year
}

# Add cookies from your request
cookies = {
    "PIB_Accessibility": "Lang=1&Region=3",
    "style": "null",
    "_ga": "GA1.1.2099942994.1738260074",
}

# Make the POST request
response = session.post(
    url,
    headers=headers,
    data=payload,
    cookies=cookies
)

# Parse the response
soup = BeautifulSoup(response.text, 'html.parser')

In [11]:
soup


<!DOCTYPE HTML>

<html lang="en">
<meta charset="utf-8"/>
<meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<meta content="public" http-equiv="Cache-control"/>
<meta content="Press Information Bureau (PIB) is the nodal agency of the Government of India to disseminate information to the print and electronic media on government policies, programmes, initiatives and achievements." name="description">
<meta content="Press Information Bureau, PIB, Government of India, Indian Government news, press releases, government updates, official news, India policies, national events, government schemes, Indian news portal" name="keywords"/>
<head id="Head1"><title>
	All Press Release: Press Information Bureau
</title><meta content="930300783691811" property="fb:app_id"/><link href="https://static.pib.gov.in/WriteReadData/specificdocs/photo/2022/apr/ph20224636301.jpg" rel="icon" type="image/jpg"/><link href="https://static.pib.gov.in/writereaddata/css/style3.1.css" rel="styleshe

In [12]:
# soup = BeautifulSoup(rawData, 'html.parser')
l = [loc.text.strip() for loc in soup.find_all('h3', class_ = 'font104')]
data = {}

for i,j in zip(range(len(l)), l):
    names = []
    links = []
    for k in (soup.find_all('ul', class_ = 'leftul')[i].find_all('li')):
        names.append(k.text.strip())
            # print(names)

    for k in soup.find_all('ul', class_ = 'leftul')[i].find_all('li'):
        links.append('https://pib.gov.in/' + k.find('a').attrs['href'])
            # print(links)    
        data[j] = (names, links)

In [13]:
data

{"President's Secretariat": (['Press Release Posted On: 31 Jan 2025',
   'Address By The Hon’ble President Of India Smt. Droupadi Murmu to Parliament Posted On: 31 Jan 2025',
   'PRESIDENT OF INDIA HOSTS PRESIDENT OF INDONESIA Posted On: 25 Jan 2025',
   'ADDRESS TO THE NATION BY THE HON’BLE PRESIDENT OF INDIA SMT. DROUPADI MURMU ON THE EVE OF REPUBLIC DAY 2025 Posted On: 25 Jan 2025',
   'PRESIDENT OF INDIA GRACES THE 15TH NATIONAL VOTERS’ DAY CELEBRATIONS Posted On: 25 Jan 2025',
   'PRESIDENT OF INDIA TO ADDRESS THE NATION TOMORROW ON THE EVE OF REPUBLIC DAY Posted On: 24 Jan 2025',
   'PRESIDENT OF INDIA PAYS FLORAL TRIBUTES TO NETAJI SUBHAS CHANDRA BOSE ON HIS BIRTH ANNIVERSARY Posted On: 23 Jan 2025',
   'PROBATIONERS OF INDIAN DEFENCE ACCOUNTS SERVICE AND INDIAN TELECOMMUNICATIONS SERVICE CALL ON THE PRESIDENT Posted On: 22 Jan 2025',
   'AMRIT UDYAN TO OPEN FOR PUBLIC FROM FEBRUARY 2 Posted On: 21 Jan 2025',
   'PRESIDENT OF INDIA PRESENTS SPORTS AND ADVENTURE AWARDS 2024 Poste

In [ ]:

# Extract ASP.NET hidden fields


# Prepare the payload with your selections


# Extract press releases - adjust selector based on actual page structure
results = []
for row in soup.select('#ctl00_ContentPlaceHolder1_UpdatePanel1 .release-content'):
    title = row.find('h3').get_text(strip=True)
    date = row.find('span', class_='datetime').get_text(strip=True)
    link = row.find('a')['href']
    
    results.append({
        'title': title,
        'date': date,
        'link': link
    })

# Print results
print(f"Found {len(results)} press releases:")
for item in results:
    print(f"\nTitle: {item['title']}")
    print(f"Date: {item['date']}")
    print(f"Link: {item['link']}")

In [40]:
def htmlFilesCreator(month, year):
    import requests
    from bs4 import BeautifulSoup

    calendar = {
        1: 'January',
        2: 'February',
        3: 'March',
        4: 'April',
        5: 'May',
        6: 'June',
        7: 'July',
        8: 'August',
        9: 'September',
        10: 'October',
        11: 'November',
        12: 'December'
    }
    
# Set up session and headers
    session = requests.Session()
    headers = {
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/132.0.0.0 Safari/537.36 Edg/132.0.0.0",
        "Origin": "https://pib.gov.in",
        "Referer": "https://pib.gov.in/allRel.aspx?reg=3&lang=1",
        "Sec-Fetch-Dest": "document",
        "Sec-Fetch-Mode": "navigate",
        "Sec-Fetch-Site": "same-origin",
    }

    # Initial GET request to get ViewState and validation fields
    url = "https://pib.gov.in/allRel.aspx"
    response = session.get(url, headers=headers)
    soup = BeautifulSoup(response.text, 'html.parser')
    viewstate = soup.find('input', {'id': '__VIEWSTATE'})['value']
    event_validation = soup.find('input', {'id': '__EVENTVALIDATION'})['value']
    viewstate_generator = soup.find('input', {'id': '__VIEWSTATEGENERATOR'})['value']
    
    
    payload = {
    "__EVENTTARGET": "ctl00$ContentPlaceHolder1$ddlday",
    "__EVENTARGUMENT": "",
    "__LASTFOCUS": "",
    "__VIEWSTATE": viewstate,
    "__VIEWSTATEGENERATOR": viewstate_generator,
    "__VIEWSTATEENCRYPTED": "",
    "__EVENTVALIDATION": event_validation,
    "ctl00$Bar1$ddlregion": "3",  # Region code
    "ctl00$Bar1$ddlLang": "1",    # Language code
    "ctl00$ContentPlaceHolder1$hydregionid": "3",
    "ctl00$ContentPlaceHolder1$hydLangid": "1",
    "ctl00$ContentPlaceHolder1$ddlMinistry": "0",  # 0 = All Ministry
    "ctl00$ContentPlaceHolder1$ddlday": "0",       # 0 = All Days
    "ctl00$ContentPlaceHolder1$ddlMonth": "1",     # 1 = January
    "ctl00$ContentPlaceHolder1$ddlYear": "2025",   # Selected year
}

# Add cookies from your request
    cookies = {
        "PIB_Accessibility": "Lang=1&Region=3",
        "style": "null",
        "_ga": "GA1.1.2099942994.1738260074",
    }

    # Make the POST request
    response = session.post(
        url,
        headers=headers,
        data=payload,
        cookies=cookies
    )

    # Parse the response
    soup = BeautifulSoup(response.text, 'html.parser')
    relevant_soup = soup.find('div', class_ = 'content-area')
    
    with open(f'{calendar[month]}_{year}.html', 'w', encoding="utf-8") as f:
        f.write(str(relevant_soup))


In [20]:
l = [loc.text.strip() for loc in soup.find_all('h3', class_ = 'font104')]

In [27]:
content = soup.find('div', class_ = 'content-area')

In [28]:
len(content)

68

In [29]:
l = [loc.text.strip() for loc in content.find_all('h3', class_ = 'font104')]
data = {}

for i,j in zip(range(len(l)), l):
    names = []
    links = []
    for k in (content.find_all('ul', class_ = 'leftul')[i].find_all('li')):
        names.append(k.text.strip())
            # print(names)

    for k in content.find_all('ul', class_ = 'leftul')[i].find_all('li'):
        links.append('https://pib.gov.in/' + k.find('a').attrs['href'])
            # print(links)    
        data[j] = (names, links)

In [26]:
l

[]

In [37]:
len(data["President's Secretariat"][0])

22

In [38]:
total = 0
for i in data.keys():
    total+=len(data[i][0])
    

In [39]:
total

1155

In [41]:
htmlFilesCreator(1, 2025)

In [46]:
from ..FinalApplicationFiles.scraper.scraperFunction import htmlFilesCreator

ImportError: attempted relative import with no known parent package

In [49]:
def htmlFilesCreator(month, year):
    import requests
    from bs4 import BeautifulSoup
    import os

    calendar = {
        1: 'January',
        2: 'February',
        3: 'March',
        4: 'April',
        5: 'May',
        6: 'June',
        7: 'July',
        8: 'August',
        9: 'September',
        10: 'October',
        11: 'November',
        12: 'December'
    }
    
# Set up session and headers
    session = requests.Session()
    headers = {
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/132.0.0.0 Safari/537.36 Edg/132.0.0.0",
        "Origin": "https://pib.gov.in",
        "Referer": "https://pib.gov.in/allRel.aspx?reg=3&lang=1",
        "Sec-Fetch-Dest": "document",
        "Sec-Fetch-Mode": "navigate",
        "Sec-Fetch-Site": "same-origin",
    }

    # Initial GET request to get ViewState and validation fields
    url = "https://pib.gov.in/allRel.aspx"
    response = session.get(url, headers=headers)
    soup = BeautifulSoup(response.text, 'html.parser')
    viewstate = soup.find('input', {'id': '__VIEWSTATE'})['value']
    event_validation = soup.find('input', {'id': '__EVENTVALIDATION'})['value']
    viewstate_generator = soup.find('input', {'id': '__VIEWSTATEGENERATOR'})['value']
    
    
    payload = {
    "__EVENTTARGET": "ctl00$ContentPlaceHolder1$ddlday",
    "__EVENTARGUMENT": "",
    "__LASTFOCUS": "",
    "__VIEWSTATE": viewstate,
    "__VIEWSTATEGENERATOR": viewstate_generator,
    "__VIEWSTATEENCRYPTED": "",
    "__EVENTVALIDATION": event_validation,
    "ctl00$Bar1$ddlregion": "3",  # Region code
    "ctl00$Bar1$ddlLang": "1",    # Language code
    "ctl00$ContentPlaceHolder1$hydregionid": "3",
    "ctl00$ContentPlaceHolder1$hydLangid": "1",
    "ctl00$ContentPlaceHolder1$ddlMinistry": "0",  # 0 = All Ministry
    "ctl00$ContentPlaceHolder1$ddlday": "0",       # 0 = All Days
    "ctl00$ContentPlaceHolder1$ddlMonth": "1",     # 1 = January
    "ctl00$ContentPlaceHolder1$ddlYear": "2025",   # Selected year
}

# Add cookies from your request
    cookies = {
        "PIB_Accessibility": "Lang=1&Region=3",
        "style": "null",
        "_ga": "GA1.1.2099942994.1738260074",
    }

    # Make the POST request
    response = session.post(
        url,
        headers=headers,
        data=payload,
        cookies=cookies
    )

    
    # Parse the response
    soup = BeautifulSoup(response.text, 'html.parser')
    relevant_soup = soup.find('div', class_ = 'content-area')
   
    directory = f'HTML{str(year)[2:]}' # Takes last 2 digits of year (e.g., 24 for 2024)
    directory = os.path.join('ScraperFiles', directory)
    # Create directory if it doesn't exist
    if not os.path.exists(directory):
        os.makedirs(directory)
    
    # Save file in the year-specific directory
    file_path = os.path.join(directory, f'{calendar[month]}{str(year)[2:]}.html')
    
    with open(file_path, 'w', encoding="utf-8") as f:
        f.write(str(relevant_soup))
    print("HTML file created successfully!")

In [51]:
for i in range(1, 13):
    htmlFilesCreator(i, 2025)

HTML file created successfully!
HTML file created successfully!
HTML file created successfully!
HTML file created successfully!
HTML file created successfully!
HTML file created successfully!
HTML file created successfully!
HTML file created successfully!
HTML file created successfully!
HTML file created successfully!
HTML file created successfully!
HTML file created successfully!
